In [1]:
import json
from collections import defaultdict, OrderedDict
import numpy as np
import os, shutil
import subprocess
import json
from typing import List, Dict, Optional, Any, Tuple
import glob

In [2]:
import textworld
import textworld.gym
import gym

In [3]:
import twutils
from twutils.file_helpers import count_iter_items, parse_gameid, split_gamename
from twutils.twlogic import filter_observables
from twutils.redis_ids import *


In [4]:
#TW_TRAINING_DIR = f'{TW_DATA_BASEDIR}/train/'
TW_TRAINING_DIR = '/ssd2tb/ftwc/games/train/'
TW_VALIDATION_DIR = '/ssd2tb/ftwc/games/valid/'
TW_TEST_DIR = '/ssd2tb/ftwc/games/test/'

PTHRU_DIR = '/ssd2tb/ftwc/playthru_data/'
RANDOM_SEED = 42


In [5]:
import tokenizers
from tokenizers import Tokenizer
from tokenizers.pre_tokenizers import Whitespace
from tokenizers.pre_tokenizers import WhitespaceSplit
from tokenizers.pre_tokenizers import Punctuation

from tokenizers import normalizers
from tokenizers.normalizers import Lowercase, Strip, Replace, Sequence


In [6]:
from tokenizers.trainers import UnigramTrainer

In [7]:
special_tokens = ['<PAD>', '<UNK>', '<S>', '</S>', '<bos>', '<eos>', '<NONE>', '<sep>',]
                  
    #  '---Exits---']  #, COMMAND_TOKEN]

                 # '+open', '+closed', '+roasted', '+baked', '+fried', '+raw',
                 # '+sliced', '+diced', '+chopped', '++Carrying:', ]
normalizer = normalizers.Sequence([Strip(), Lowercase()])
pre_tokenizer = Whitespace()

model = tokenizers.models.WordLevel(unk_token='<UNK>')
# model = tokenizers.models.WordPiece()
tokenizer = Tokenizer(model=model)


tokenizer.add_special_tokens(special_tokens)
# tokenizer.add_tokens(['---Exits---'])  #, COMMAND_TOKEN,])
# tokenizer.add_tokens(['frosted-glass'])
# tokenizer.add_tokens(['[UNK]'])  #'++Carrying:', 'hello', '+how', 'today'])
tokenizer.normalizer = normalizer
tokenizer.pre_tokenizer = pre_tokenizer

# filelist = glob.glob(PTHRU_DIR+"miniset/*.pthru")
filelist = glob.glob(PTHRU_DIR+"valid/*.pthru")
filelist.extend( glob.glob(PTHRU_DIR+"test/*.pthru"))
filelist.extend( glob.glob(PTHRU_DIR+"train/*.pthru"))

filelist.extend( glob.glob(PTHRU_DIR+"*.textds"))
# token_strs = [tok for (tok, span) in pre_tokenizer.pre_tokenize_str(str1)]
# print(token_strs)
print(len(filelist))
#unigram_trainer = tokenizers.trainers.UnigramTrainer()
trainer = tokenizers.trainers.WordLevelTrainer(vocab_size=500, special_tokens=special_tokens)
#trainer = tokenizers.trainers.WordPieceTrainer(vocab_size=100)

tokenizer.train(files=filelist, trainer=trainer)


5179


In [8]:
str1 = " ++Carrying: Hello there, +how are   you \n today? "

print(normalizer.normalize_str(str1))
token_strs = [tok for (tok, span) in pre_tokenizer.pre_tokenize_str(str1)]
print(token_strs)

encoding = tokenizer.encode(str1)
print(encoding.tokens)

++carrying: hello there, +how are   you 
 today?
['++', 'Carrying', ':', 'Hello', 'there', ',', '+', 'how', 'are', 'you', 'today', '?']
['++', 'carrying', ':', 'hello', 'there', ',', '+', 'how', 'are', 'you', 'today', '?']


In [9]:
print(filelist[-1])

/ssd2tb/ftwc/playthru_data/mingpt-test.textds


In [10]:
pthru_str = open(filelist[0], 'r').read()
#print(pthru_str)
pthru_encoding = tokenizer.encode(pthru_str)

In [11]:
pthru_str = open(filelist[-1], 'r').read()
#print(pthru_str)
pthru_encoding = tokenizer.encode(pthru_str)

In [12]:
token_list = pthru_encoding.tokens[:]
print(len(token_list), token_list)

314887 ['>>>[', 'start', ']<<<', '|', '---------', 'do', ':', 'find', 'kitchen', ',', 'read', 'cookbook', ',', 'eat', 'meal', '.', '|', '-=', 'corridor', '=-', '|', 'exits', '|', 'east', 'to', 'unknown', ';', '|', 'south', 'to', 'unknown', ';', '|', '>>>[', 'go', 'south', ']<<<', '|', 'you', 'go', 'south', '.', '|', '-=', 'livingroom', '=-', '|', 'on', 'sofa', ':', 'nothing', ';', '|', 'exits', '|', 'east', 'to', 'unknown', ';', '|', 'north', 'to', 'corridor', ';', '|', 'south', 'to', 'unknown', ';', '|', '>>>[', 'go', 'south', ']<<<', '|', 'you', 'go', 'south', '.', '|', '-=', 'kitchen', '=-', '|', 'in', '+', 'open', 'fridge', ':', 'yellow', 'bell', 'pepper', ',', '+', 'raw', 'yellow', 'onion', ',', '+', 'raw', 'red', 'hot', 'pepper', ';', '|', 'in', '+', 'closed', 'oven', ':', 'unknown', ';', '|', 'on', 'table', ':', 'cookbook', ';', '|', 'on', 'counter', ':', '+', 'roasted', 'green', 'hot', 'pepper', ',', '+', 'roasted', 'red', 'potato', ',', '+', 'raw', 'orange', 'bell', 'pepper', 

In [13]:
decoded = tokenizer.decode(pthru_encoding.ids, skip_special_tokens=False)
print(decoded)

>>>[ start ]<<< | --------- do : find kitchen , read cookbook , eat meal . | -= corridor =- | exits | east to unknown ; | south to unknown ; | >>>[ go south ]<<< | you go south . | -= livingroom =- | on sofa : nothing ; | exits | east to unknown ; | north to corridor ; | south to unknown ; | >>>[ go south ]<<< | you go south . | -= kitchen =- | in + open fridge : yellow bell pepper , + raw yellow onion , + raw red hot pepper ; | in + closed oven : unknown ; | on table : cookbook ; | on counter : + roasted green hot pepper , + roasted red potato , + raw orange bell pepper , + raw red apple , + raw yellow potato , knife ; | on stove : nothing ; | exits | east + open plain door to unknown ; | north to livingroom ; | >>>[ open oven ]<<< | you open the oven . | -= kitchen =- | in + open fridge : yellow bell pepper , + raw yellow onion , + raw red hot pepper ; | in + open oven : nothing ; | on table : cookbook ; | on counter : + roasted green hot pepper , + roasted red potato , + raw orange 

In [14]:
# help(tokenizer)

In [16]:
vocab = tokenizer.get_vocab(with_added_tokens=True)
slist = [(vocab[k], k) for k in vocab.keys()]
print(sorted(slist))
tokenizer.save('ftwc_tokenizer_new.json', pretty=True)


[(0, '<PAD>'), (1, '<UNK>'), (2, '<S>'), (3, '</S>'), (4, '<bos>'), (5, '<eos>'), (6, '<NONE>'), (7, '<sep>'), (8, ';'), (9, '+'), (10, ','), (11, ':'), (12, '|'), (13, 'raw'), (14, 'on'), (15, 'open'), (16, 'nothing'), (17, 'to'), (18, 'red'), (19, 'pepper'), (20, 'potato'), (21, '---------'), (22, 'in'), (23, 'unknown'), (24, '.'), (25, 'meal'), (26, 'yellow'), (27, 'kitchen'), (28, 'cookbook'), (29, 'door'), (30, '>>>['), (31, '-='), (32, '=-'), (33, ']<<<'), (34, 'onion'), (35, 'you'), (36, 'bell'), (37, 'do'), (38, 'oven'), (39, 'carrying'), (40, 'exits'), (41, 'the'), (42, 'fridge'), (43, 'table'), (44, 'knife'), (45, 'counter'), (46, 'stove'), (47, 'prepare'), (48, 'chop'), (49, 'east'), (50, 'north'), (51, 'west'), (52, 'south'), (53, 'go'), (54, 'acquire'), (55, 'hot'), (56, 'apple'), (57, 'chicken'), (58, 'white'), (59, 'purple'), (60, 'closed'), (61, 'read'), (62, 'eat'), (63, 'pork'), (64, 'banana'), (65, 'orange'), (66, 'of'), (67, 'cheese'), (68, 'block'), (69, 'slice'), 

In [20]:
tokenizer2 = Tokenizer.from_file('/ssd2tb/ftwc/ftwc_tokenizer.json')
vocab2 = tokenizer2.get_vocab(with_added_tokens=True)
print(len(vocab), len(vocab2))
for i in range(max(len(vocab), len(vocab2))):
    tok1 = tokenizer.id_to_token(i)
    if tok1 is None:
        tok1 = 'NONE'
    tok2 = tokenizer2.id_to_token(i)
    if tok2 is None:
        tok2 = 'NONE'
    if tok2 != tok1:
        tok1 = "* "+tok1
    else:
        tok1 = "  "+tok1
    print(f"{i}:{tok1:9s}\t{tok2}")
print()

156 157
0:  <PAD>  	<PAD>
1:  <UNK>  	<UNK>
2:  <S>    	<S>
3:  </S>   	</S>
4:* <bos>  	<|>
5:* <eos>  	<NONE>
6:* <NONE> 	<bos>
7:* <sep>  	<eos>
8:* ;      	<sep>
9:* +      	;
10:* ,      	+
11:  :      	:
12:* |      	,
13:  raw    	raw
14:  on     	on
15:  open   	open
16:  nothing	nothing
17:  to     	to
18:* red    	---
19:* pepper 	in
20:* potato 	red
21:* ---------	unknown
22:* in     	pepper
23:* unknown	door
24:* .      	]<<<
25:* meal   	-=
26:* yellow 	>>>[
27:* kitchen	=-
28:* cookbook	.
29:* door   	you
30:* >>>[   	potato
31:* -=     	carrying
32:* =-     	exits
33:* ]<<<   	kitchen
34:* onion  	oven
35:* you    	cookbook
36:* bell   	the
37:* do     	fridge
38:* oven   	knife
39:* carrying	table
40:* exits  	counter
41:* the    	yellow
42:* fridge 	stove
43:* table  	east
44:* knife  	north
45:* counter	west
46:* stove  	south
47:* prepare	go
48:* chop   	onion
49:* east   	bell
50:* north  	closed
51:* west   	meal
52:* south  	hot
53:* go     	apple
54:* acquire	pat

In [21]:
pthru_encoding2 = tokenizer2.encode(pthru_str)
token_list2 = pthru_encoding2.tokens[:]
print(len(token_list2))
print(token_list2)
assert token_list2 == token_list

314887
['>>>[', 'start', ']<<<', '|', '---------', 'do', ':', 'find', 'kitchen', ',', 'read', 'cookbook', ',', 'eat', 'meal', '.', '|', '-=', 'corridor', '=-', '|', 'exits', '|', 'east', 'to', 'unknown', ';', '|', 'south', 'to', 'unknown', ';', '|', '>>>[', 'go', 'south', ']<<<', '|', 'you', 'go', 'south', '.', '|', '-=', 'livingroom', '=-', '|', 'on', 'sofa', ':', 'nothing', ';', '|', 'exits', '|', 'east', 'to', 'unknown', ';', '|', 'north', 'to', 'corridor', ';', '|', 'south', 'to', 'unknown', ';', '|', '>>>[', 'go', 'south', ']<<<', '|', 'you', 'go', 'south', '.', '|', '-=', 'kitchen', '=-', '|', 'in', '+', 'open', 'fridge', ':', 'yellow', 'bell', 'pepper', ',', '+', 'raw', 'yellow', 'onion', ',', '+', 'raw', 'red', 'hot', 'pepper', ';', '|', 'in', '+', 'closed', 'oven', ':', 'unknown', ';', '|', 'on', 'table', ':', 'cookbook', ';', '|', 'on', 'counter', ':', '+', 'roasted', 'green', 'hot', 'pepper', ',', '+', 'roasted', 'red', 'potato', ',', '+', 'raw', 'orange', 'bell', 'pepper', 

In [15]:
decoded2 = tokenizer2.decode(pthru_encoding.ids, skip_special_tokens=False)
print(decoded2)

kitchen a oven in =- , block . + roasted you + glass pepper ]<<< the . cookbook door : open west , : raw white potato + : raw sliced frosted - + : raw -= exits red + : raw nothing potato + : raw parsley + : raw from ; door : diced stove , >>>[ ; on go , you + south ; on onion , : raw nothing unknown ; on bell , to ; yellow meal : open leg pantry read carrying --- >>>[ ; apple --- >>>[ ; counter , : raw do red + : screen floor workbench + : raw floor eat + : raw acquire chicken + : screen acquire exits red + : raw nothing fried red + : chopped nothing find ; in =- , block . + roasted you + glass pepper ]<<< kitchen open stove oven fridge open east stove ]<<< the . cookbook door : open west , : raw white potato + : raw sliced frosted - + : raw -= exits red + : raw nothing potato + : raw parsley + : raw from ; door : open stove , to ; on go , you + south ; on onion , : raw nothing unknown ; on bell , to ; yellow meal : open leg pantry read carrying --- >>>[ ; apple --- >>>[ ; counter , : 

In [16]:
decoded == decoded2

False

In [17]:
print(tokenizer.get_vocab_size(with_added_tokens=True))

165


In [18]:
pthrus_all = open('/ssd2tb/ftwc/mingpt-valid-all.pthru', 'r').read()
encoded_all = tokenizer.encode(pthrus_all)

FileNotFoundError: [Errno 2] No such file or directory: '/ssd2tb/ftwc/mingpt-valid-all.pthru'

In [19]:
len(encoded_all.tokens)

NameError: name 'encoded_all' is not defined

In [ ]:
str_out = tokenizer.decode(encoded_all.ids, skip_special_tokens=False)
print(str_out[0:200])

In [ ]:
"<UNK>" in str_out

In [ ]:
tokenizer.token_to_id('>>>['), tokenizer.token_to_id(']<<<')


In [ ]:
vocab_dict = tokenizer.get_vocab(with_added_tokens=True)
print(len(vocab_dict))
print(tokenizer.get_vocab_size(with_added_tokens=True))

In [ ]:
print(vocab_dict)

In [ ]:
print(tokenizer.id_to_token(155))

In [ ]:
tokenizer.token_to_id('>>>[')